In [110]:
import os
import pydicom
from pydicom.filereader import read_dicomdir
import matplotlib.pyplot as plt
import pandas as pd
from collections import Counter
import glob
import numpy as np
import datetime
import re
import dicom2nifti
import nibabel as nib
from nibabel.testing import data_path
import matplotlib.pyplot as plt
from dipy.align.reslice import reslice

from sklearn.model_selection import train_test_split
import matplotlib.pyplot as plt

In [2]:
os.chdir('/home/hwi3319/CQ500')

In [2]:
data_dir = '/home/hwi3319/CQ500'

In [3]:
def RenameFolders(data_dir):
    for dir_entry in os.scandir(path = data_dir):
        if dir_entry.is_dir():
            dir_re = re.search(pattern = "CQ500CT([0-9]*) CQ500CT([0-9]*)", string = dir_entry.name)
            dir_new = "CQ500-CT-%s" % dir_re.group(1)
            os.rename(data_dir + dir_entry.name, data_dir + dir_new)

In [4]:
good_dicom_list = []
# create a dictionary of all the sub directories for each subject directory
# loop through subject directories
for dir_entry in os.scandir(path = data_dir):
    subject_dir_dict = dict()
    if dir_entry.is_dir() and re.match("CQ500CT([0-9]*) CQ500CT([0-9]*)", dir_entry.name):
        subject_dir_dict[dir_entry.name] = list()
        
        # loop through sub-directories and exclude some by name
        for sub_dir in os.scandir(dir_entry.path + "/Unknown Study/"):
            if sub_dir.is_dir() and not re.search("(POST|(?<!PRE )CONTRAST|BONE| C | C$)", sub_dir.name):
                dcm_files = glob.glob(sub_dir.path + "/*.dcm")
                dicom_data = pydicom.read_file(dcm_files[0])

                # add info for these sub-directories to a dictionary
                sub_info = [sub_dir.name, dicom_data.PixelSpacing[0], dicom_data.PixelSpacing[1], dicom_data.SliceThickness, len(dcm_files)]
                subject_dir_dict[dir_entry.name].append(sub_info)


        # warn if no usable directories found
        if(len(subject_dir_dict[dir_entry.name]) < 1):
            # print("Warning: {subject} found no usable subdirectories".format(subject=dir_entry.name))
            subject_dir_dict.pop(dir_entry.name)    # remove the entry from the dict
            continue

        elif(len(subject_dir_dict[dir_entry.name]) > 1):
            # parse the remaining directories to find the best candidate scan
            subject_scans = subject_dir_dict[dir_entry.name]

            scans_info = np.array(subject_scans)
            sorted_idx = np.argsort(scans_info[:, 3])

            # check for a 5mm slice scan
            if(float(scans_info[sorted_idx[-1], 3]) == 5.0):
                
                # check if there are two 5mm slice scans
                if(float(scans_info[sorted_idx[-2], 3]) == 5.0):
                    # if more than one 5mm slice scan, use the scan with fewest slices
                    scans_info = scans_info[scans_info[:, 3].astype(float) == 5.0]          # keep only the 5mm slice scans
                    sorted_slices_idx = np.argsort(scans_info[:, 4])
                    subject_dir_dict[dir_entry.name] = [subject_dir_dict[dir_entry.name][sorted_slices_idx[-1]]]  # replace with fewest slices study
                    if(subject_dir_dict[dir_entry.name][0][4] < 30):
                        print("Warning: Fewer than 30 slices for {}".format(dir_entry.path + "/" + subject_dir_dict[dir_entry.name][0][0]))
                else:
                    subject_dir_dict[dir_entry.name] = [subject_dir_dict[dir_entry.name][sorted_idx[-1]]]         # replace with the 5mm study

            else:   # if no 5mm slice scans, so choose the smallest
                subject_dir_dict[dir_entry.name] = [subject_dir_dict[dir_entry.name][sorted_idx[0]]]              # replace with the smallest slice scan


        # convert the chosen study folder to nifti for further processing
        print(dir_entry.path + "/Unknown Study/" + subject_dir_dict[dir_entry.name][0][0])
        d_path = dir_entry.path + "/Unknown Study/" + subject_dir_dict[dir_entry.name][0][0]
        good_dicom_list.append(d_path)

/home/hwi3319/CQ500/CQ500CT0 CQ500CT0/Unknown Study/CT Plain
/home/hwi3319/CQ500/CQ500CT1 CQ500CT1/Unknown Study/CT 2.55mm
/home/hwi3319/CQ500/CQ500CT10 CQ500CT10/Unknown Study/CT PLAIN THIN
/home/hwi3319/CQ500/CQ500CT100 CQ500CT100/Unknown Study/CT Plain THIN
/home/hwi3319/CQ500/CQ500CT101 CQ500CT101/Unknown Study/CT Plain
/home/hwi3319/CQ500/CQ500CT102 CQ500CT102/Unknown Study/CT Plain
/home/hwi3319/CQ500/CQ500CT103 CQ500CT103/Unknown Study/CT 55mm Plain
/home/hwi3319/CQ500/CQ500CT104 CQ500CT104/Unknown Study/CT Plain
/home/hwi3319/CQ500/CQ500CT105 CQ500CT105/Unknown Study/CT PRE CONTRAST 5MM STD
/home/hwi3319/CQ500/CQ500CT106 CQ500CT106/Unknown Study/CT 55mm Plain
/home/hwi3319/CQ500/CQ500CT107 CQ500CT107/Unknown Study/CT Thin Plain-2
/home/hwi3319/CQ500/CQ500CT108 CQ500CT108/Unknown Study/CT 5mm
/home/hwi3319/CQ500/CQ500CT109 CQ500CT109/Unknown Study/CT 5mm
/home/hwi3319/CQ500/CQ500CT11 CQ500CT11/Unknown Study/CT 55mm Plain
/home/hwi3319/CQ500/CQ500CT110 CQ500CT110/Unknown Study/CT

/home/hwi3319/CQ500/CQ500CT219 CQ500CT219/Unknown Study/CT 5mm
/home/hwi3319/CQ500/CQ500CT22 CQ500CT22/Unknown Study/CT Plain
/home/hwi3319/CQ500/CQ500CT220 CQ500CT220/Unknown Study/CT Plain
/home/hwi3319/CQ500/CQ500CT221 CQ500CT221/Unknown Study/CT Plain
/home/hwi3319/CQ500/CQ500CT222 CQ500CT222/Unknown Study/CT PRE CONTRAST 5MM STD
/home/hwi3319/CQ500/CQ500CT223 CQ500CT223/Unknown Study/CT Plain
/home/hwi3319/CQ500/CQ500CT224 CQ500CT224/Unknown Study/CT Plain 3mm
/home/hwi3319/CQ500/CQ500CT225 CQ500CT225/Unknown Study/CT Plain
/home/hwi3319/CQ500/CQ500CT226 CQ500CT226/Unknown Study/CT 5mm
/home/hwi3319/CQ500/CQ500CT227 CQ500CT227/Unknown Study/CT 55mm Plain
/home/hwi3319/CQ500/CQ500CT228 CQ500CT228/Unknown Study/CT Plain
/home/hwi3319/CQ500/CQ500CT229 CQ500CT229/Unknown Study/CT PRE CONTRAST 5MM STD
/home/hwi3319/CQ500/CQ500CT23 CQ500CT23/Unknown Study/CT PRE CONTRAST 5MM STD
/home/hwi3319/CQ500/CQ500CT230 CQ500CT230/Unknown Study/CT SOFT THIN
/home/hwi3319/CQ500/CQ500CT231 CQ500CT23

/home/hwi3319/CQ500/CQ500CT362 CQ500CT362/Unknown Study/CT 55mm Plain
/home/hwi3319/CQ500/CQ500CT363 CQ500CT363/Unknown Study/CT Plain
/home/hwi3319/CQ500/CQ500CT364 CQ500CT364/Unknown Study/CT Plain 3mm
/home/hwi3319/CQ500/CQ500CT365 CQ500CT365/Unknown Study/CT 55mm Plain
/home/hwi3319/CQ500/CQ500CT366 CQ500CT366/Unknown Study/CT Plain THIN
/home/hwi3319/CQ500/CQ500CT367 CQ500CT367/Unknown Study/CT 55mm Plain
/home/hwi3319/CQ500/CQ500CT368 CQ500CT368/Unknown Study/CT Plain
/home/hwi3319/CQ500/CQ500CT369 CQ500CT369/Unknown Study/CT C-2
/home/hwi3319/CQ500/CQ500CT37 CQ500CT37/Unknown Study/CT Plain
/home/hwi3319/CQ500/CQ500CT370 CQ500CT370/Unknown Study/CT Plain
/home/hwi3319/CQ500/CQ500CT371 CQ500CT371/Unknown Study/CT Plain 3mm
/home/hwi3319/CQ500/CQ500CT372 CQ500CT372/Unknown Study/CT 55mm Plain
/home/hwi3319/CQ500/CQ500CT373 CQ500CT373/Unknown Study/CT 55mm Plain
/home/hwi3319/CQ500/CQ500CT374 CQ500CT374/Unknown Study/CT Plain THIN
/home/hwi3319/CQ500/CQ500CT375 CQ500CT375/Unknown S

/home/hwi3319/CQ500/CQ500CT481 CQ500CT481/Unknown Study/CT Plain
/home/hwi3319/CQ500/CQ500CT482 CQ500CT482/Unknown Study/CT PRE CONTRAST 5MM STD
/home/hwi3319/CQ500/CQ500CT483 CQ500CT483/Unknown Study/CT 55mm Plain
/home/hwi3319/CQ500/CQ500CT484 CQ500CT484/Unknown Study/CT Plain THIN
/home/hwi3319/CQ500/CQ500CT485 CQ500CT485/Unknown Study/CT Plain
/home/hwi3319/CQ500/CQ500CT486 CQ500CT486/Unknown Study/CT Plain
/home/hwi3319/CQ500/CQ500CT487 CQ500CT487/Unknown Study/CT Plain 3mm
/home/hwi3319/CQ500/CQ500CT488 CQ500CT488/Unknown Study/CT 5mm
/home/hwi3319/CQ500/CQ500CT489 CQ500CT489/Unknown Study/CT 5mm
/home/hwi3319/CQ500/CQ500CT49 CQ500CT49/Unknown Study/CT PRE CONTRAST 5MM STD
/home/hwi3319/CQ500/CQ500CT490 CQ500CT490/Unknown Study/CT Plain
/home/hwi3319/CQ500/CQ500CT5 CQ500CT5/Unknown Study/CT Plain 3mm
/home/hwi3319/CQ500/CQ500CT50 CQ500CT50/Unknown Study/CT 5mm
/home/hwi3319/CQ500/CQ500CT51 CQ500CT51/Unknown Study/CT Plain
/home/hwi3319/CQ500/CQ500CT52 CQ500CT52/Unknown Study/CT P

In [5]:
good_dicom_list

['/home/hwi3319/CQ500/CQ500CT0 CQ500CT0/Unknown Study/CT Plain',
 '/home/hwi3319/CQ500/CQ500CT1 CQ500CT1/Unknown Study/CT 2.55mm',
 '/home/hwi3319/CQ500/CQ500CT10 CQ500CT10/Unknown Study/CT PLAIN THIN',
 '/home/hwi3319/CQ500/CQ500CT100 CQ500CT100/Unknown Study/CT Plain THIN',
 '/home/hwi3319/CQ500/CQ500CT101 CQ500CT101/Unknown Study/CT Plain',
 '/home/hwi3319/CQ500/CQ500CT102 CQ500CT102/Unknown Study/CT Plain',
 '/home/hwi3319/CQ500/CQ500CT103 CQ500CT103/Unknown Study/CT 55mm Plain',
 '/home/hwi3319/CQ500/CQ500CT104 CQ500CT104/Unknown Study/CT Plain',
 '/home/hwi3319/CQ500/CQ500CT105 CQ500CT105/Unknown Study/CT PRE CONTRAST 5MM STD',
 '/home/hwi3319/CQ500/CQ500CT106 CQ500CT106/Unknown Study/CT 55mm Plain',
 '/home/hwi3319/CQ500/CQ500CT107 CQ500CT107/Unknown Study/CT Thin Plain-2',
 '/home/hwi3319/CQ500/CQ500CT108 CQ500CT108/Unknown Study/CT 5mm',
 '/home/hwi3319/CQ500/CQ500CT109 CQ500CT109/Unknown Study/CT 5mm',
 '/home/hwi3319/CQ500/CQ500CT11 CQ500CT11/Unknown Study/CT 55mm Plain',
 '

In [92]:
os.chdir('/home/hwi3319/COMP_SCI_496_SML')
f = open('GoodDicomFolderList.txt','w+')
for p in good_dicom_list:
    p+='\n'
    f.writelines(p)
f.close()


# Run ConvertAllToNifti.sh before the following steps

In [133]:
all_nii_gz = []
for d_p in good_dicom_list:
    os.chdir(d_p)
    flagA = True
    for f in os.listdir():
        if f.endswith('_Tilt_1.nii.gz'):
            all_nii_gz.append(d_p + '/' + f)
            flagA = False
            break
    if(flagA):
         for f in os.listdir():
            if f.endswith('.nii.gz'):
                all_nii_gz.append(d_p + '/' + f)
                break

In [136]:
all_nii_gz

['/home/hwi3319/CQ500/CQ500CT0 CQ500CT0/Unknown Study/CT Plain/CT Plain_Plain_0_2_Tilt_1.nii.gz',
 '/home/hwi3319/CQ500/CQ500CT1 CQ500CT1/Unknown Study/CT 2.55mm/CT 2.55mm_2.5_5mm_0_2_Tilt_1.nii.gz',
 '/home/hwi3319/CQ500/CQ500CT10 CQ500CT10/Unknown Study/CT PLAIN THIN/CT PLAIN THIN_PLAIN_THIN_0_3_Tilt_1.nii.gz',
 '/home/hwi3319/CQ500/CQ500CT100 CQ500CT100/Unknown Study/CT Plain THIN/CT Plain THIN_Plain_THIN_0_3.nii.gz',
 '/home/hwi3319/CQ500/CQ500CT101 CQ500CT101/Unknown Study/CT Plain/CT Plain_Plain_0_2_Tilt_1.nii.gz',
 '/home/hwi3319/CQ500/CQ500CT102 CQ500CT102/Unknown Study/CT Plain/CT Plain_Plain_0_2.nii.gz',
 '/home/hwi3319/CQ500/CQ500CT104 CQ500CT104/Unknown Study/CT Plain/CT Plain_Plain_0_2_Tilt_1.nii.gz',
 '/home/hwi3319/CQ500/CQ500CT105 CQ500CT105/Unknown Study/CT PRE CONTRAST 5MM STD/CT PRE CONTRAST 5MM STD_PRE_CONTRAST_5MM_STD_0_4.nii.gz',
 '/home/hwi3319/CQ500/CQ500CT107 CQ500CT107/Unknown Study/CT Thin Plain-2/CT Thin Plain-2_Thin_Plain_0_6.nii.gz',
 '/home/hwi3319/CQ500/

In [137]:
# nifti_folder = 'Nifti_Files'

#here we should provide a list of scans that need to be resliced
#or we just list everything in the folder
scan_list = all_nii_gz

#the resolution of reslicing
new_zooms = (1., 1., 5.)

for i in scan_list:
    scan_name = i

    img = nib.load(scan_name)
    data = img.get_fdata()

    #maybe we reslcie everything?

    affine = img.affine
    zooms = img.header.get_zooms()[:3]

    data2, affine2 = reslice(data, affine, zooms, new_zooms)

    img2 = nib.Nifti1Image(data2, affine2)

    new_name = scan_name[:-7] + '_5mm' + '.nii'
    nib.save(img2, new_name)


In [138]:
all_nii_5mm = []
for d_p in good_dicom_list:
    os.chdir(d_p)
    for f in os.listdir():
        if f.endswith('_5mm.nii'):
            all_nii_5mm.append(d_p + '/' + f)

In [139]:
all_nii_5mm

['/home/hwi3319/CQ500/CQ500CT0 CQ500CT0/Unknown Study/CT Plain/CT Plain_Plain_0_2_Tilt_1_5mm.nii',
 '/home/hwi3319/CQ500/CQ500CT1 CQ500CT1/Unknown Study/CT 2.55mm/CT 2.55mm_2.5_5mm_0_2_Tilt_1_5mm.nii',
 '/home/hwi3319/CQ500/CQ500CT10 CQ500CT10/Unknown Study/CT PLAIN THIN/CT PLAIN THIN_PLAIN_THIN_0_3_Tilt_1_5mm.nii',
 '/home/hwi3319/CQ500/CQ500CT100 CQ500CT100/Unknown Study/CT Plain THIN/CT Plain THIN_Plain_THIN_0_3_5mm.nii',
 '/home/hwi3319/CQ500/CQ500CT101 CQ500CT101/Unknown Study/CT Plain/CT Plain_Plain_0_2_Tilt_1_5mm.nii',
 '/home/hwi3319/CQ500/CQ500CT102 CQ500CT102/Unknown Study/CT Plain/CT Plain_Plain_0_2_5mm.nii',
 '/home/hwi3319/CQ500/CQ500CT104 CQ500CT104/Unknown Study/CT Plain/CT Plain_Plain_0_2_Tilt_1_5mm.nii',
 '/home/hwi3319/CQ500/CQ500CT105 CQ500CT105/Unknown Study/CT PRE CONTRAST 5MM STD/CT PRE CONTRAST 5MM STD_PRE_CONTRAST_5MM_STD_0_4_5mm.nii',
 '/home/hwi3319/CQ500/CQ500CT107 CQ500CT107/Unknown Study/CT Thin Plain-2/CT Thin Plain-2_Thin_Plain_0_6_5mm.nii',
 '/home/hwi33

In [308]:
label_file_name = 'summary_label.csv'
nifti_folder = '/home/hwi3319/CQ500'
new_size = (224, 224)
#the following 2 parameters can not be 1 at the same time
normalize_img = 1
#if 1, normalize to 0~255
#if 0, don't normalize, use raw numbers
three_channels = 1
#if 1, create 3 channels instead of the original 1 channel
#if 0, use the original 1 channle
#for the 3 channels, we use the following window:
#brain window: (l = 40, w = 80), i.e. 0~80 (everything <0 is 0, everything >80 is 255)
#bone window: (l = 500, w = 3000), i.e. -1000~2000
#subdural window: (l = 175, w = 50), i.e. 150~200
#l is the center of the luminance and w is the width
channel_param = ((0, 80), (-1000, 2000), (150, 200))

#we will only include data that is within this range after reslicing to 5mm
max_num_slice = 50
min_num_slice = 28

In [248]:
scan_list = []
for i in range(len(all_nii_5mm)):
    scan_list.append(int(all_nii_5mm[i].split('CQ500CT')[1]))

In [249]:
#we need to count how many slices are in each nifti file, probably go with the smallest number
#then for each scan, get the middle slices with that number
#after preprocessing, we don't have scans from 120, 163, 336 and 491
scan_list = np.array(scan_list)
num_slice = np.empty((scan_list.shape[0],))

j=0
for ss in scan_list:
    #for each scan read in the nifti file
    i = ss
    scan_fn = all_nii_5mm[j]
    img = nib.load(scan_fn)
    img_data = img.get_fdata()
    num_slice[j] = img_data.shape[2]
    j=j+1

num_slice = num_slice.astype(int)

scan_list=np.squeeze(scan_list)
#create a pandas dataframe with the index and num_slice
num_slice_df = pd.DataFrame({'scan_id':scan_list, 'num_slice':num_slice})

num_slice_df = num_slice_df[num_slice_df.num_slice <= max_num_slice]
num_slice_df = num_slice_df[num_slice_df.num_slice >= min_num_slice]

#num_slice_df has all of the information about number of slices in each scan

In [365]:
def create_channel(img, channel_min, channel_max):
    #this function will create channeled data based on the original single values data
    
    img_channel = img.copy()
    img_channel[img_channel <= channel_min] = channel_min
    img_channel[img_channel >= channel_max] = channel_max
    if np.amax(img_channel) - np.amin(img_channel) == 0:
        img_channel = img_channel
    else: 
        img_channel = 255 * (img_channel-np.amin(img_channel))/(np.amax(img_channel) - np.amin(img_channel))
    return img_channel

In [250]:
os.chdir('/home/hwi3319/COMP_SCI_496_SML')

In [382]:
#now we will read in each scan, select min_num_slices from the middle of the scan, and
#generate a numpy file for each slice, with the corresponding label!

final_scan_list = num_slice_df['scan_id']

labels = pd.read_csv(label_file_name)

#use the scan name as index
labels.set_index('name', inplace=True)

x = 0
for ss in final_scan_list:
    #for each scan read in the nifti file
    scan_fn = all_nii_5mm[num_slice_df.index[num_slice_df['scan_id'] == ss][0]]
    img = nib.load(scan_fn)
    img_data = img.get_fdata()
    
    #check the number of slices for this scan, and select the middle 28
    current_num_slice = img_data.shape[2]
    
    if current_num_slice > min_num_slice:
        #more than 28 slices, we need to select the middle one
        if current_num_slice%2 == 0:
            #this is an even number
            start_slice = int((current_num_slice - min_num_slice)/2)
            
        else:
            #this is an odd number
            start_slice = int((current_num_slice -1 - min_num_slice)/2)
        
        #in python, the end_slice is actually not included in the range
        end_slice = int(start_slice + min_num_slice)
    else:
        start_slice = 0
        end_slice = int(start_slice + min_num_slice)
     
    #grab the label for this scan
    current_label = labels[['ICH', 'IPH', 'IVH', 'SDH', 'EDH', 'SAH',
       'BleedLocation-Left', 'BleedLocation-Right', 'ChronicBleed', 'Fracture',
       'CalvarialFracture', 'OtherFracture', 'MassEffect', 'MidlineShift']][labels.index == 'CQ500-CT-'+str(ss)]
    current_scan_id = ss
    
    
    #now we generate data for slices in the range between start_slice and end_slice
    slice_index = 0 #this starts from 0, not the same as the original slice number in the original scan
    for j in range(start_slice, end_slice):
        #resize
        one_img_resize = resize(img_data[:, :, j], new_size)
        if normalize_img == 1:
            #normalize to 0~255
            img_processed = 255 * (one_img_resize-np.amin(one_img_resize))/(np.amax(one_img_resize) - np.amin(one_img_resize))      
        else:
            if three_channels == 1:
                #be careful! now each image will be 3D
                
                #first create an empty numpy array for the channeled ones
                img_processed=np.empty((new_size[0], new_size[1], len(channel_param)))
            
                for c in range(0, len(channel_param)):
                    img_processed[:, :, c] = create_channel(one_img_resize, channel_param[c][0], channel_param[c][1])
                    
            else:
                img_processed = one_img_resize
                
        #save this img_processed as a numpy array
        img_file_name = 'Slices/' + 'CQ500-CT-' + str(ss) + '_Slice' + str(slice_index) + '.npy'
        np.save(img_file_name, img_processed)
        
        #create a dictionary for label and scan_id and save it
        label_info = {'scan_id': current_scan_id, 'label': current_label}
        img_label_file_name = 'Labels/' + 'CQ500-CT-' + str(ss) + '_Slice' + str(slice_index) + '.npy'
        np.save(img_label_file_name, label_info)
        
        print(label_info)
        
        slice_index = slice_index+1
        
    x+=1

{'scan_id': 0, 'label':               ICH    IPH    IVH    SDH    EDH    SAH  BleedLocation-Left  \
name                                                                       
CQ500-CT-0  False  False  False  False  False  False               False   

            BleedLocation-Right  ChronicBleed  Fracture  CalvarialFracture  \
name                                                                         
CQ500-CT-0                False         False     False              False   

            OtherFracture  MassEffect  MidlineShift  
name                                                 
CQ500-CT-0          False       False         False  }
{'scan_id': 0, 'label':               ICH    IPH    IVH    SDH    EDH    SAH  BleedLocation-Left  \
name                                                                       
CQ500-CT-0  False  False  False  False  False  False               False   

            BleedLocation-Right  ChronicBleed  Fracture  CalvarialFracture  \
name              

{'scan_id': 0, 'label':               ICH    IPH    IVH    SDH    EDH    SAH  BleedLocation-Left  \
name                                                                       
CQ500-CT-0  False  False  False  False  False  False               False   

            BleedLocation-Right  ChronicBleed  Fracture  CalvarialFracture  \
name                                                                         
CQ500-CT-0                False         False     False              False   

            OtherFracture  MassEffect  MidlineShift  
name                                                 
CQ500-CT-0          False       False         False  }
{'scan_id': 0, 'label':               ICH    IPH    IVH    SDH    EDH    SAH  BleedLocation-Left  \
name                                                                       
CQ500-CT-0  False  False  False  False  False  False               False   

            BleedLocation-Right  ChronicBleed  Fracture  CalvarialFracture  \
name              

{'scan_id': 1, 'label':              ICH   IPH    IVH    SDH    EDH   SAH  BleedLocation-Left  \
name                                                                    
CQ500-CT-1  True  True  False  False  False  True                True   

            BleedLocation-Right  ChronicBleed  Fracture  CalvarialFracture  \
name                                                                         
CQ500-CT-1                 True         False     False              False   

            OtherFracture  MassEffect  MidlineShift  
name                                                 
CQ500-CT-1          False        True          True  }
{'scan_id': 1, 'label':              ICH   IPH    IVH    SDH    EDH   SAH  BleedLocation-Left  \
name                                                                    
CQ500-CT-1  True  True  False  False  False  True                True   

            BleedLocation-Right  ChronicBleed  Fracture  CalvarialFracture  \
name                                

{'scan_id': 1, 'label':              ICH   IPH    IVH    SDH    EDH   SAH  BleedLocation-Left  \
name                                                                    
CQ500-CT-1  True  True  False  False  False  True                True   

            BleedLocation-Right  ChronicBleed  Fracture  CalvarialFracture  \
name                                                                         
CQ500-CT-1                 True         False     False              False   

            OtherFracture  MassEffect  MidlineShift  
name                                                 
CQ500-CT-1          False        True          True  }
{'scan_id': 10, 'label':               ICH   IPH    IVH    SDH    EDH    SAH  BleedLocation-Left  \
name                                                                      
CQ500-CT-10  True  True  False  False  False  False                True   

             BleedLocation-Right  ChronicBleed  Fracture  CalvarialFracture  \
name                        

{'scan_id': 10, 'label':               ICH   IPH    IVH    SDH    EDH    SAH  BleedLocation-Left  \
name                                                                      
CQ500-CT-10  True  True  False  False  False  False                True   

             BleedLocation-Right  ChronicBleed  Fracture  CalvarialFracture  \
name                                                                          
CQ500-CT-10                False         False     False              False   

             OtherFracture  MassEffect  MidlineShift  
name                                                  
CQ500-CT-10          False       False         False  }
{'scan_id': 10, 'label':               ICH   IPH    IVH    SDH    EDH    SAH  BleedLocation-Left  \
name                                                                      
CQ500-CT-10  True  True  False  False  False  False                True   

             BleedLocation-Right  ChronicBleed  Fracture  CalvarialFracture  \
name           

...

{'scan_id': 97, 'label':                ICH    IPH    IVH    SDH    EDH    SAH  BleedLocation-Left  \
name                                                                        
CQ500-CT-97  False  False  False  False  False  False               False   

             BleedLocation-Right  ChronicBleed  Fracture  CalvarialFracture  \
name                                                                          
CQ500-CT-97                False         False     False              False   

             OtherFracture  MassEffect  MidlineShift  
name                                                  
CQ500-CT-97          False       False         False  }
{'scan_id': 97, 'label':                ICH    IPH    IVH    SDH    EDH    SAH  BleedLocation-Left  \
name                                                                        
CQ500-CT-97  False  False  False  False  False  False               False   

             BleedLocation-Right  ChronicBleed  Fracture  CalvarialFracture  \
nam

{'scan_id': 97, 'label':                ICH    IPH    IVH    SDH    EDH    SAH  BleedLocation-Left  \
name                                                                        
CQ500-CT-97  False  False  False  False  False  False               False   

             BleedLocation-Right  ChronicBleed  Fracture  CalvarialFracture  \
name                                                                          
CQ500-CT-97                False         False     False              False   

             OtherFracture  MassEffect  MidlineShift  
name                                                  
CQ500-CT-97          False       False         False  }
{'scan_id': 97, 'label':                ICH    IPH    IVH    SDH    EDH    SAH  BleedLocation-Left  \
name                                                                        
CQ500-CT-97  False  False  False  False  False  False               False   

             BleedLocation-Right  ChronicBleed  Fracture  CalvarialFracture  \
nam

{'scan_id': 98, 'label':                ICH    IPH    IVH    SDH    EDH    SAH  BleedLocation-Left  \
name                                                                        
CQ500-CT-98  False  False  False  False  False  False               False   

             BleedLocation-Right  ChronicBleed  Fracture  CalvarialFracture  \
name                                                                          
CQ500-CT-98                False         False     False              False   

             OtherFracture  MassEffect  MidlineShift  
name                                                  
CQ500-CT-98          False       False         False  }
{'scan_id': 98, 'label':                ICH    IPH    IVH    SDH    EDH    SAH  BleedLocation-Left  \
name                                                                        
CQ500-CT-98  False  False  False  False  False  False               False   

             BleedLocation-Right  ChronicBleed  Fracture  CalvarialFracture  \
nam

{'scan_id': 98, 'label':                ICH    IPH    IVH    SDH    EDH    SAH  BleedLocation-Left  \
name                                                                        
CQ500-CT-98  False  False  False  False  False  False               False   

             BleedLocation-Right  ChronicBleed  Fracture  CalvarialFracture  \
name                                                                          
CQ500-CT-98                False         False     False              False   

             OtherFracture  MassEffect  MidlineShift  
name                                                  
CQ500-CT-98          False       False         False  }
{'scan_id': 98, 'label':                ICH    IPH    IVH    SDH    EDH    SAH  BleedLocation-Left  \
name                                                                        
CQ500-CT-98  False  False  False  False  False  False               False   

             BleedLocation-Right  ChronicBleed  Fracture  CalvarialFracture  \
nam

{'scan_id': 99, 'label':                ICH    IPH    IVH    SDH    EDH    SAH  BleedLocation-Left  \
name                                                                        
CQ500-CT-99  False  False  False  False  False  False               False   

             BleedLocation-Right  ChronicBleed  Fracture  CalvarialFracture  \
name                                                                          
CQ500-CT-99                False         False     False              False   

             OtherFracture  MassEffect  MidlineShift  
name                                                  
CQ500-CT-99          False       False         False  }
{'scan_id': 99, 'label':                ICH    IPH    IVH    SDH    EDH    SAH  BleedLocation-Left  \
name                                                                        
CQ500-CT-99  False  False  False  False  False  False               False   

             BleedLocation-Right  ChronicBleed  Fracture  CalvarialFracture  \
nam